We will analyze https://research.google.com/audioset///dataset/emergency_vehicle.html

# Preample

In [1]:
import json
import pandas as pd
import numpy as np
import os
import librosa
import IPython.display as ipd
import random
from sklearn.model_selection import train_test_split

In [2]:
# reproducibility
np.random.seed(1337)
random.seed(42)

# Checking quality of the 'unbalanced' dataset

In [11]:
path_train_unbalanced_positives = "/nfs/students/summer-term-2020/project-4/data/dataset1/download/training_unbalanced/positive/"

In [51]:
random.seed(42)
(dirpath, dirnames, filenames) = next(os.walk(path_train_unbalanced_positives))
filesToCheckManually = random.sample(filenames,30)

for filename in filesToCheckManually:
    full_file_path = dirpath+filename
    print(full_file_path)
    y, sr = librosa.load(full_file_path, sr=8000)
    ipd.display(ipd.Audio(y, rate=sr))

/nfs/students/summer-term-2020/project-4/data/dataset1/download/training_unbalanced/positive/cuk682f1Qwo.wav


/nfs/students/summer-term-2020/project-4/data/dataset1/download/training_unbalanced/positive/ZwfFTYNrrlg.wav


/nfs/students/summer-term-2020/project-4/data/dataset1/download/training_unbalanced/positive/-ZtZOcg3s7M.wav


/nfs/students/summer-term-2020/project-4/data/dataset1/download/training_unbalanced/positive/MuXlximELks.wav


/nfs/students/summer-term-2020/project-4/data/dataset1/download/training_unbalanced/positive/NJ4Vs9XVid4.wav


...

/nfs/students/summer-term-2020/project-4/data/dataset1/download/training_unbalanced/positive/oP_6BGapCw0.wav


/nfs/students/summer-term-2020/project-4/data/dataset1/download/training_unbalanced/positive/UXZ7V8RKa9Q.wav


/nfs/students/summer-term-2020/project-4/data/dataset1/download/training_unbalanced/positive/aJrXtD-wz84.wav


/nfs/students/summer-term-2020/project-4/data/dataset1/download/training_unbalanced/positive/yOI134PGxxM.wav


/nfs/students/summer-term-2020/project-4/data/dataset1/download/training_unbalanced/positive/1V_o0pCQEqY.wav


All sound like emergency vehicles!

# Train/Valid/Test split

In [3]:
path_train_unbalanced_negatives = "/nfs/students/summer-term-2020/project-4/data/dataset1/download/training_unbalanced/negative/"
path_train_unbalanced_positives = "/nfs/students/summer-term-2020/project-4/data/dataset1/download/training_unbalanced/positive/"

path_train_balanced_negatives = "/nfs/students/summer-term-2020/project-4/data/dataset1/download/training_balanced/negative/"
path_train_balanced_positives = "/nfs/students/summer-term-2020/project-4/data/dataset1/download/training_balanced/positive/"

path_eval_balanced_negatives = "/nfs/students/summer-term-2020/project-4/data/dataset1/download/eval_balanced/negative/"
path_eval_balanced_positives = "/nfs/students/summer-term-2020/project-4/data/dataset1/download/eval_balanced/positive/"

In [4]:
positive_class_paths = [path_train_unbalanced_positives,
                        path_train_balanced_positives,
                        path_eval_balanced_positives]

negative_class_paths = [path_train_unbalanced_negatives,
                        path_train_balanced_negatives,
                        path_eval_balanced_negatives]

In [5]:
def mergeSources(paths):
    class_filenames = []
    class_paths=[]

    for path in paths:
        (dirpath, dirnames, filenames) = next(os.walk(path))

        for filename in filenames:
            if filename == 'meta.csv':
                continue
                
            if filename not in class_filenames:
                class_filenames.append(filename)
                class_paths.append(dirpath + filename)
                
    return class_paths

In [6]:
positive_class = mergeSources(positive_class_paths)
negative_class = mergeSources(negative_class_paths)

In [7]:
print(len(positive_class))
print(len(negative_class))

4217
23318


In [8]:
# balancing negative class
random.seed(42)
balanced_class_size = len(positive_class)
balanced_negative_class = random.sample(negative_class, balanced_class_size)

In [9]:
# shuffle for similar distribution properties
random.seed(1337)
final_dataset = random.sample(positive_class+balanced_negative_class, len(positive_class+balanced_negative_class))

In [10]:
len(final_dataset)

8434

In [11]:
# final split
train_paths, valid_paths, test_paths = np.split(final_dataset, [int(.6*len(final_dataset)), int(.8*len(final_dataset))])

In [12]:
print(len(train_paths))
print(len(valid_paths))
print(len(test_paths))

5060
1687
1687


# Obtain metadata

In [13]:
def loadJsonFile(path):
    if path[-5:] == '.json':
        return json.load(open(path))

path_ontology = "/nfs/students/summer-term-2020/project-4/data/dataset1/ontology/ontology.json"
ontology = loadJsonFile(path_ontology)

In [15]:
ontology_id_name_mapping = {}

for entry in ontology:
    ontology_id_name_mapping[entry['id']] = entry['name']

In [16]:
def loadMetaFiles(paths):
    meta_files = []
    for path in paths:
        (dirpath, dirnames, filenames) = next(os.walk(path))
        for filename in filenames:
            if filename != 'meta.csv':
                continue
            meta_files.append(pd.read_csv(dirpath + filename, index_col=0))
        
    return pd.concat(meta_files, axis=0)

In [17]:
df_meta = loadMetaFiles(positive_class_paths + negative_class_paths)

In [18]:
df_meta.head(1)

start_seconds  end_seconds  \
--gKfbzT1VY           20.0         30.0   

                                               positive_labels  
--gKfbzT1VY  "/m/012ndj,/m/03j1ly,/m/07r04,/m/07yv9,/t/dd00...

In [19]:
ontology_id_name_mapping['/m/012ndj']

'Fire engine, fire truck (siren)'

In [20]:
def createFinalDataset(datasetFiles):
    final_set = []
    
    for filePath in datasetFiles:
        
        # (...)/dataset1/download/training_unbalanced/negative/9kHMnPosPzw.wav'
        name = filePath.split('/')[-1][:-4]
        classification = filePath.split('/')[-2]
        source = filePath.split('/')[-3]
        
        # see samples of df_meta and ontology_id_name_mapping above
        labels = df_meta.loc[name]['positive_labels'][1:-1].split(',')
        label_names = [ontology_id_name_mapping[label] for label in labels]
        
        sample = {'youtube_id': name,
                  'start_seconds': df_meta.loc[name]['start_seconds'],
                  'end_seconds': df_meta.loc[name]['end_seconds'],
                  'binary_class': classification,
                  'labels': labels,
                  'label_names': label_names,
                  'source': source, 
                  'path': filePath}
        
        final_set.append(sample)
        
    return final_set

In [21]:
train = createFinalDataset(train_paths)
valid = createFinalDataset(valid_paths)
test = createFinalDataset(test_paths)

In [22]:
# negative sample
train[0]

{'youtube_id': '9kHMnPosPzw',
 'start_seconds': 21.0,
 'end_seconds': 31.0,
 'binary_class': 'negative',
 'labels': ['/m/07yv9', '/m/0k4j', '/t/dd00066'],
 'label_names': ['Vehicle', 'Car', 'Medium engine (mid frequency)'],
 'source': 'training_unbalanced',
 'path': '/nfs/students/summer-term-2020/project-4/data/dataset1/download/training_unbalanced/negative/9kHMnPosPzw.wav'}

In [23]:
# positive sample
train[1]

{'youtube_id': 'NNjnnHQmE-k',
 'start_seconds': 0.0,
 'end_seconds': 10.0,
 'binary_class': 'positive',
 'labels': ['/m/012ndj', '/m/03j1ly', '/m/03kmc9'],
 'label_names': ['Fire engine, fire truck (siren)',
  'Emergency vehicle',
  'Siren'],
 'source': 'training_unbalanced',
 'path': '/nfs/students/summer-term-2020/project-4/data/dataset1/download/training_unbalanced/positive/NNjnnHQmE-k.wav'}

# Save dataset

In [24]:
path_training_paths = "/nfs/students/summer-term-2020/project-4/data/dataset1/finalDataset/training.json"
path_validation_paths = "/nfs/students/summer-term-2020/project-4/data/dataset1/finalDataset/validation.json"
path_testing_paths = "/nfs/students/summer-term-2020/project-4/data/dataset1/finalDataset/testing.json"

In [25]:
def saveDataset(dataset, path):
    f = open(path, "w")
    f.write(json.dumps(dataset))
    f.close()

In [26]:
saveDataset(train, path_training_paths)
saveDataset(valid, path_validation_paths)
saveDataset(test,  path_testing_paths)